# 1. 模型搭建

# 1.1. 初始化函数

In [1]:
import torch.nn as nn
import torch.nn.functional as F
import torch
 
# 初始化函数
def weights_init_normal(m):
    classname = m.__class__.__name__ # m作为一个形参，原则上可以传递很多的内容，为了实现多实参传递，
                                     # 每一个modules要给出自己的name. 所以这句话就是返回m的名字。
    if classname.find("Conv") != -1: # find()函数，实现查找classname中是否含有conv字符，没有返回-1；有返回0.
        torch.nn.init.normal_(m.weight.data, 0.0, 0.02) # m.weight.data表示需要初始化的权重。 
                                                        # nn.init.normal_()表示随机初始化采用正态分布，均值为0，标准差为0.02.
        if hasattr(m, "bias") and m.bias is not None:
            torch.nn.init.constant_(m.bias.data, 0.0) # nn.init.constant_()表示将偏差定义为常量0 
    elif classname.find("BatchNorm2d") != -1:
        torch.nn.init.normal_(m.weight.data, 1.0, 0.02)
        torch.nn.init.constant_(m.bias.data, 0.0)

# RESNET 模块定义

In [2]:
class ResidualBlock(nn.Module):
    def __init__(self, in_features):
        super(ResidualBlock, self).__init__()
 
        self.block = nn.Sequential(
            nn.ReflectionPad2d(1),
            nn.Conv2d(in_features, in_features, 3),
            nn.InstanceNorm2d(in_features),
            nn.ReLU(inplace=True),
            nn.ReflectionPad2d(1),
            nn.Conv2d(in_features, in_features, 3),
            nn.InstanceNorm2d(in_features),
        )
 
    def forward(self, x):
        return x + self.block(x)

# 模型定义

In [3]:
# 生成器定义：模型一上来就是3个“卷积块”，
# 每个卷积块包含：一个2D卷积层，一个Instance Normalization层和一个ReLU。
# 这3个“卷积块”是用来降采样的。然后是9个“残差块”，每个残差块包含2个卷积层，每个卷积层后面都有一个Instance Normalization层，
# 第一个Instance Normalization层后面是ReLU激活函数，这些使用残差连接。
# 然后过3个“上采样块”，每个块包含一个2D转置卷积层，1个Instance Normalization和1个ReLU激活函数。
# 最后一层是一个2D卷积层，使用tanh作为激活函数，该层生成的形状为(256，256，3)的图像。
# 这个Generator的输入和输出的大小是一摸一样的，都是(256，256，3)。

In [4]:
class GeneratorResNet(nn.Module):
    def __init__(self, input_shape, num_residual_blocks):
        super(GeneratorResNet, self).__init__()
 
        channels = input_shape[0]
 
        # Initial convolution block
        # 初始化卷积模块
        out_features = 64 # out_features 指的是输出的二维张量的大小
        model = [
            nn.ReflectionPad2d(channels), # 对四周都填充channels行
            nn.Conv2d(channels, out_features, 7), # 归一化
            nn.InstanceNorm2d(out_features),
            nn.ReLU(inplace=True), # 会修改输入对象的值
        ]
        in_features = out_features
 
        # Downsampling
        # 降采样 3个卷积模块
        for _ in range(2):
            out_features *= 2
            model += [
                nn.Conv2d(in_features, out_features, 3, stride=2, padding=1),
                nn.InstanceNorm2d(out_features),
                nn.ReLU(inplace=True),
            ]
            in_features = out_features
 
        # Residual blocks
        # resnet模块  num_residual_blocks=9
        for _ in range(num_residual_blocks):
            model += [ResidualBlock(out_features)]
 
        # Upsampling
        # 上采样
        for _ in range(2):
            out_features //= 2
            model += [
                nn.Upsample(scale_factor=2), # 空间尺寸的乘数(multiplier for spatial size)
                nn.Conv2d(in_features, out_features, 3, stride=1, padding=1),
                nn.InstanceNorm2d(out_features),
                nn.ReLU(inplace=True),
            ]
            in_features = out_features
 
        # Output layer
        # 输出层
        model += [nn.ReflectionPad2d(channels), nn.Conv2d(out_features, channels, 7), nn.Tanh()]
 
        self.model = nn.Sequential(*model)
 
    def forward(self, x):
        return self.model(x)

In [5]:
# 判别器定义：判别网络的架构类似于PatchGAN中的判别网络架构，是一个包含几个卷积块的深度卷积神经网络。

In [6]:
class Discriminator(nn.Module):
    def __init__(self, input_shape):
        super(Discriminator, self).__init__()
 
        channels, height, width = input_shape
 
        # Calculate output shape of image discriminator (PatchGAN)
        # 计算判别器输出的图片大小(PatchGAN)
        self.output_shape = (1, height // 2 ** 4, width // 2 ** 4)
 
        def discriminator_block(in_filters, out_filters, normalize=True):
            """Returns downsampling layers of each discriminator block"""
            layers = [nn.Conv2d(in_filters, out_filters, 4, stride=2, padding=1)]
            if normalize:
                layers.append(nn.InstanceNorm2d(out_filters))
            layers.append(nn.LeakyReLU(0.2, inplace=True))
            # LeakyReLU(x)={ x>0 =x ， x≤0 =ax}
            # Leaky ReLU函数通过把x xx的非常小的线性分量给予负输入0.01 x 0.01x0.01x来调整负值的零梯度问题。

            return layers
 
        self.model = nn.Sequential(
            *discriminator_block(channels, 64, normalize=False),
            *discriminator_block(64, 128),
            *discriminator_block(128, 256),
            *discriminator_block(256, 512),
            nn.ZeroPad2d((1, 0, 1, 0)), # 零填充
            nn.Conv2d(512, 1, 4, padding=1)
        )
 
    def forward(self, img):
        return self.model(img)

# 2. 读取数据

In [7]:
import glob
import random
import os
 
from torch.utils.data import Dataset
from PIL import Image
import torchvision.transforms as transforms
 
# 如果输入的数据集是灰度图像，将图片转化为rgb图像
def to_rgb(image):
    rgb_image = Image.new("RGB", image.size) # 这个函数创建一幅给定模式（mode）和尺寸（size）的图片。
                                             # 如果省略 color 参数，则创建的图片被黑色填充满，如果 color 参数是 None 值，则图片还没初始化
    rgb_image.paste(image) # 1).粘贴新图片至图片中，box 参数可以为 2-元组（upper, left）或是 4-元组（left, upper, right, lower），
                           # 或者是 None（0, 0）。2). 功能同上。不过是将指定位置填充为某种颜色。 
    return rgb_image
 
# 对数据进行读取
class ImageDataset(Dataset):
    def __init__(self, root, transforms_=None, unaligned=False, mode="train"): # (root = "./", unaligned=True:非对其数据)
        self.transform = transforms.Compose(transforms_) # transform变为tensor数据
        self.unaligned = unaligned
 
        self.files_A = sorted(glob.glob(os.path.join(root, "trainA") + "/*.*")) # 返回所有匹配的文件路径列表，连接root和trainA/B路径
        self.files_B = sorted(glob.glob(os.path.join(root, "trainB") + "/*.*")) # "./trainB/*.*"
        
        '''
        also
        self.files_A = sorted(glob.glob(os.path.join(root, "%s/A" % mode) + "/*.*"))# "./trainA/*.*"
        self.files_B = sorted(glob.glob(os.path.join(root, "%s/B" % mode) + "/*.*"))
        '''
 
 
    def __getitem__(self, index):
        image_A = Image.open(self.files_A[index % len(self.files_A)]) # 在A中取一张照片
 
        if self.unaligned: # 如果采用非配对数据，在B中随机取一张
            image_B = Image.open(self.files_B[random.randint(0, len(self.files_B) - 1)]) 
        else:
            image_B = Image.open(self.files_B[index % len(self.files_B)])
 
        # Convert grayscale images to rgb
        # 如果是灰度图，把灰度图转换为RGB图
        if image_A.mode != "RGB":
            image_A = to_rgb(image_A)
        if image_B.mode != "RGB":
            image_B = to_rgb(image_B)
        
        # 把RGB图像转换为tensor图, 方便计算，返回字典数据
        item_A = self.transform(image_A)
        item_B = self.transform(image_B)
        return {"A": item_A, "B": item_B}
    
    # 获取A,B数据的长度
    def __len__(self):
        return max(len(self.files_A), len(self.files_B))

# 3. 基本功能函数实现

In [8]:
import random
import time
import datetime
import sys
 
from torch.autograd import Variable
import torch
import numpy as np
 
from torchvision.utils import save_image

# 先前生成的样本的缓冲区
class ReplayBuffer:
    def __init__(self, max_size=50):
        assert max_size > 0, "Empty buffer or trying to create a black hole. Be careful."
        self.max_size = max_size
        self.data = []
 
    def push_and_pop(self, data): # 放入一张图像，再从buffer里取一张出来
        to_return = [] # 确保数据的随机性，判断真假图片的鉴别器识别率
        for element in data.data:
            element = torch.unsqueeze(element, 0)
            if len(self.data) < self.max_size: # 最多放入50张，没满就一直添加
                self.data.append(element)
                to_return.append(element)
            else:
                if random.uniform(0, 1) > 0.5: # 满了就1/2的概率从buffer里取，或者就用当前的输入图片
                    i = random.randint(0, self.max_size - 1)
                    to_return.append(self.data[i].clone())
                    self.data[i] = element
                else:
                    to_return.append(element)
        return Variable(torch.cat(to_return))
 
 
class LambdaLR:
    def __init__(self, n_epochs, offset, decay_start_epoch): # (n_epochs = 50, offset = epoch, decay_start_epoch = 30)
        assert (n_epochs - decay_start_epoch) > 0, "Decay must start before the training session ends!" 
        # 要让n_epochs > decay_start_epoch 才可以
        self.n_epochs = n_epochs
        self.offset = offset
        self.decay_start_epoch = decay_start_epoch
 
    def step(self, epoch): # 公式 ：1-max(0, epoch - 30) / (50 - 30)
        return 1.0 - max(0, epoch + self.offset - self.decay_start_epoch) / (self.n_epochs - self.decay_start_epoch)

# 4. Cycle-GAN 实现

# 4.1. 导入相关库

In [9]:
import argparse
import os
import numpy as np
import math
import itertools
import datetime
import time
 
import torchvision.transforms as transforms
from torchvision.utils import save_image, make_grid
 
from torch.utils.data import DataLoader
from torchvision import datasets
from torch.autograd import Variable
 
import torch.nn as nn
import torch.nn.functional as F
import torch

# 4.2. 参数设置

In [10]:
'''参数表格
epoch:使用数据集的所有数据进行一次模型训练，一代训练，从第0代开始训练
n_epochs:训练的次数，默认200次
dataset_name：数据集文件夹的名字，默认"monet2photo"
batch_size：使用数据中的一部分数据进行模型权重更新的这部分数据大小，默认1,(受限于电脑性能)
lr：adam学习率
b1&b2：adam学习参数
decay_epoch：lr学习率开始衰减
n_cpu：训练过程中用到的CPU线程数目
img_height：输入图片的高度，默认256
img_width：输入图片的宽度，默认256
channels：图片的通道数，默认为彩色图片，channels=3
sample_interval：每隔一段时间对训练输出进行采样并展示，默认100 #每100次保存测试集测试结果图片
n_residual_blocks：生成器中的residual模块的数量
lambda_cyc：cycle loss权重参数
lambda_id：identity loss权重参数
'''
 
parser = argparse.ArgumentParser()
parser.add_argument("--epoch", type=int, default=0, help="epoch to start training from")
parser.add_argument("--n_epochs", type=int, default=200, help="number of epochs of training")
parser.add_argument("--dataset_name", type=str, default="monet2photo", help="name of the dataset")
parser.add_argument("--batch_size", type=int, default=1, help="size of the batches")
parser.add_argument("--lr", type=float, default=0.0002, help="adam: learning rate")
parser.add_argument("--b1", type=float, default=0.5, help="adam: decay of first order momentum of gradient")
parser.add_argument("--b2", type=float, default=0.999, help="adam: decay of first order momentum of gradient")
parser.add_argument("--decay_epoch", type=int, default=100, help="epoch from which to start lr decay")
parser.add_argument("--n_cpu", type=int, default=8, help="number of cpu threads to use during batch generation")
parser.add_argument("--img_height", type=int, default=256, help="size of image height")
parser.add_argument("--img_width", type=int, default=256, help="size of image width")
parser.add_argument("--channels", type=int, default=3, help="number of image channels")
parser.add_argument("--sample_interval", type=int, default=100, help="interval between saving generator outputs")
parser.add_argument("--checkpoint_interval", type=int, default=-1, help="interval between saving model checkpoints")
parser.add_argument("--n_residual_blocks", type=int, default=9, help="number of residual blocks in generator")
parser.add_argument("--lambda_cyc", type=float, default=10.0, help="cycle loss weight")
parser.add_argument("--lambda_id", type=float, default=5.0, help="identity loss weight")
parser.add_argument('--cuda', action='store_true', default=True, help='use GPU computation')
arg = parser.parse_args(args=[]) # 在jupyter中运行时，需要使用此行代码
print(arg)

Namespace(epoch=0, n_epochs=200, dataset_name='monet2photo', batch_size=1, lr=0.0002, b1=0.5, b2=0.999, decay_epoch=100, n_cpu=8, img_height=256, img_width=256, channels=3, sample_interval=100, checkpoint_interval=-1, n_residual_blocks=9, lambda_cyc=10.0, lambda_id=5.0, cuda=True)


In [11]:
# 创建文件夹来保存训练过程的采样输出以及保存模型
# Create sample and checkpoint directories
os.makedirs("images_modified/%s" % arg.dataset_name, exist_ok=True)
os.makedirs("saved_models_modified/%s" % arg.dataset_name, exist_ok=True)

# 4.3. 损失函数定义和初始化

In [12]:
# 初始化三个损失函数
# Losses
# MSE 二分类的交叉熵
# l1 loss在零点不平滑，用的较少。一般来说，l1正则会制造稀疏的特征，大部分无用的特征的权重会被置为0
#L1 loss用来让生成的图片和训练的目标图片尽量相似,而图像中高频的细节部分则交由GAN来处理,
#图像中的低频部分有patchGAN处理
criterion_GAN = torch.nn.MSELoss()
criterion_cycle = torch.nn.L1Loss()
criterion_identity = torch.nn.L1Loss()

# 4.4.  初始化生成器、判别器

In [13]:
# 判断电脑是否可以使用GPU进行训练
cuda = torch.cuda.is_available()
 
# input_shape保存输入图片的通道数，高度，宽度
# input_shape:(3, 256, 256)
input_shape = (arg.channels, arg.img_height, arg.img_width)
 
# 初始化四个网络(G_AB,G_BA,D_A,D_B)，创建生成器，判别器对象
# Initialize generator and discriminator
G_AB = GeneratorResNet(input_shape, arg.n_residual_blocks)
G_BA = GeneratorResNet(input_shape, arg.n_residual_blocks)
D_A = Discriminator(input_shape)
D_B = Discriminator(input_shape)

# 4.5. 导入参数

In [14]:
# 采用GPU进行训练
if arg.cuda:
    G_AB = G_AB.cuda()
    G_BA = G_BA.cuda()
    D_A = D_A.cuda()
    D_B = D_B.cuda()
    criterion_GAN.cuda()
    criterion_cycle.cuda()
    criterion_identity.cuda()

# 如果epoch == 0，初始化模型参数; 如果epoch == n, 载入训练到第n轮的预训练模型
if arg.epoch != 0:
    # Load pretrained models
    G_AB.load_state_dict(torch.load("saved_models/%s/G_AB_%d.pth" % (arg.dataset_name, arg.epoch)))
    G_BA.load_state_dict(torch.load("saved_models/%s/G_BA_%d.pth" % (arg.dataset_name, arg.epoch)))
    D_A.load_state_dict(torch.load("saved_models/%s/D_A_%d.pth" % (arg.dataset_name, arg.epoch)))
    D_B.load_state_dict(torch.load("saved_models/%s/D_B_%d.pth" % (arg.dataset_name, arg.epoch)))
else:
    # Initialize weights
    # G_AB, G_BA, D_A, D_B是我们给写的神经网络定义的类实例。apply函数会递归地搜索网络内的所有module并把参数表示的函数应用到所有的module上。
    # 也就是说apply函数，会一层一层的去拜访Generator/Discriminator网络层
    G_AB.apply(weights_init_normal)
    G_BA.apply(weights_init_normal)
    D_A.apply(weights_init_normal)
    D_B.apply(weights_init_normal)

# 4.6. 优化器设置

In [15]:
# 定义初始化模型的优化器, 优化函数的学习率为0.0002
# Optimizers
optimizer_G = torch.optim.Adam(
    itertools.chain(G_AB.parameters(), G_BA.parameters()), lr=arg.lr, betas=(arg.b1, arg.b2)
)
optimizer_D_A = torch.optim.Adam(D_A.parameters(), lr=arg.lr, betas=(arg.b1, arg.b2))
optimizer_D_B = torch.optim.Adam(D_B.parameters(), lr=arg.lr, betas=(arg.b1, arg.b2))

"""
optimizer_G = torch.optim.RMSprop(
    itertools.chain(G_AB.parameters(), G_BA.parameters()), lr=arg.lr, betas=(arg.b1, arg.b2)
)
optimizer_D_A = torch.optim.RMSprop(D_A.parameters(), lr=arg.lr)
optimizer_D_B = torch.optim.RMSprop(D_B.parameters(), lr=arg.lr)
"""

'\noptimizer_G = torch.optim.RMSprop(\n    itertools.chain(G_AB.parameters(), G_BA.parameters()), lr=arg.lr, betas=(arg.b1, arg.b2)\n)\noptimizer_D_A = torch.optim.RMSprop(D_A.parameters(), lr=arg.lr)\noptimizer_D_B = torch.optim.RMSprop(D_B.parameters(), lr=arg.lr)\n'

# 4.7. 学习率衰减

In [16]:
# torch.optim.lr_scheduler.LambdaLR里面有一个参数lr_lambda是要输入学习率，
# 这个学习率是动态变化的，由LambdaLR(arg.n_epochs, arg.epoch, arg.decay_epoch).step来获得。

# 按照epoch的次数自动调整学习率
# Learning rate update schedulers
lr_scheduler_G = torch.optim.lr_scheduler.LambdaLR(
    optimizer_G, lr_lambda=LambdaLR(arg.n_epochs, arg.epoch, arg.decay_epoch).step
)
lr_scheduler_D_A = torch.optim.lr_scheduler.LambdaLR(
    optimizer_D_A, lr_lambda=LambdaLR(arg.n_epochs, arg.epoch, arg.decay_epoch).step
)
lr_scheduler_D_B = torch.optim.lr_scheduler.LambdaLR(
    optimizer_D_B, lr_lambda=LambdaLR(arg.n_epochs, arg.epoch, arg.decay_epoch).step
)
 
Tensor = torch.cuda.FloatTensor if cuda else torch.Tensor

# 4.8. 数据读取和数据预处理

In [17]:
# 数据预处理包括resize、crop、flip、normalize等操作。

# Buffers of previously generated samples
# 先前生成的样本的缓冲区
fake_A_buffer = ReplayBuffer()
fake_B_buffer = ReplayBuffer()
 
# 图片预处理函数
# Image transformations
transforms_ = [
    transforms.Resize(int(arg.img_height * 1.12), Image.BICUBIC),  # 调整Image对象的尺寸
    transforms.RandomCrop((arg.img_height, arg.img_width)),  # 扩大后剪切成img_height*img_width大小的图片
    transforms.RandomHorizontalFlip(),  # 依据概率p对PIL图片进行水平翻转，p默认0.5
    transforms.ToTensor(),  # 转为tensor格式
    transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),  # 归一化
]
 
# print("../../data/%s" % arg.dataset_name)
# test = ImageDataset("E:\python\pytorch-gan-master\data\monet2photo" , transforms_=transforms_, unaligned=True)
 
# 加载训练数据
# Training data loader
dataloader = DataLoader(
    # ../表示当前目录的父目录, 改成自己存放文件的目录
    ImageDataset("%s" % arg.dataset_name, transforms_=transforms_, unaligned=True),
    batch_size=arg.batch_size,
    shuffle=True,  # 将数据打乱，数值越大，混乱程度越大
    # num_workers=0,
    num_workers=0,  # 线程数
    drop_last =True,
)
 
# 测试数据加载
# Test data loader
val_dataloader = DataLoader(
    ImageDataset("%s" % arg.dataset_name, transforms_=transforms_, unaligned=True, mode="test"),
    batch_size=5,
    shuffle=True,
    num_workers=0,
    drop_last=True,
)

C:\Users\BiXY\anaconda3\envs\mmcv\lib\site-packages\torchvision\transforms\transforms.py:332: UserWarning: Argument interpolation should be of type InterpolationMode instead of int. Please, use InterpolationMode enum.
  warnings.warn(


# 4.9. 保存训练结果的样本

In [18]:
# 定义测试数据喂进网络的输出展示函数
# 每间隔100次打印图片
def sample_images(batches_done): # （100/200/300/400...）
    """Saves a generated sample from the test set"""
    imgs = next(iter(val_dataloader)) # 取一张图像 
    G_AB.eval()
    G_BA.eval()
    real_A = Variable(imgs["A"].type(Tensor)) # 取一张真A
    fake_B = G_AB(real_A) # 用真A生成假B
    real_B = Variable(imgs["B"].type(Tensor)) # 取一张真B
    fake_A = G_BA(real_B) # 用真B生成假A
    # Arange images along x-axis
    # make_grid():用于把几个图像按照网格排列的方式绘制出来
    real_A = make_grid(real_A, nrow=5, normalize=True)
    real_B = make_grid(real_B, nrow=5, normalize=True)
    fake_A = make_grid(fake_A, nrow=5, normalize=True)
    fake_B = make_grid(fake_B, nrow=5, normalize=True)
    # Arange images along y-axis
    # 把以上图像都拼接起来，保存为一张大图片
    image_grid = torch.cat((real_A, fake_B, real_B, fake_A), 1)
    save_image(image_grid, "images_modified/%s/%s.png" % (arg.dataset_name, batches_done), normalize=False)

In [19]:
# 写gp函数并添加进loss_D 
from torch import autograd
def gp(D,r_imgs, f_imgs):
    Tensor = torch.cuda.FloatTensor
    alpha = Tensor(np.random.random((r_imgs.size(0), 3, 256, 256)))
    interpolates = (alpha*r_imgs + (1 - alpha)*f_imgs).requires_grad_(True)
    d_interpolates = D(interpolates)
    fake = Variable(Tensor(np.ones((real_A.size(0), *D.output_shape))), requires_grad=False)
    gradients = autograd.grad(
        outputs=d_interpolates,
        inputs=interpolates,
        grad_outputs=fake,
        create_graph=True,
        retain_graph=True,
        only_inputs=True,
    )[0]
    gradients = gradients.view(gradients.size(0), -1)
    gradient_penalty = ((gradients.norm(1, dim=1) - 1)**2).mean()
    return gradient_penalty

# 4.10. 开始训练和保存模型

In [20]:
from tqdm.notebook import tqdm

# ----------
#  Training
#  开始训练
# ----------
 
prev_time = time.time() # 开始时间
for epoch in range(arg.epoch, arg.n_epochs): # for epoch in (0, 200)
    for i, batch in enumerate(tqdm(dataloader)): # batch is a dict, batch['A']:(1, 3, 256, 256), batch['B']:(1, 3, 256, 256)
 
        # 设置模型输入
        # Set model input
        # 读取数据集中的真图片
        # 将tensor变成Variable放入计算图中，tensor变成variable之后才能进行反向传播求梯度
        real_A = Variable(batch["A"].type(Tensor)) # 真图像A
        real_B = Variable(batch["B"].type(Tensor)) # 真图像B
 
        # 对抗生成网络中的真实图片和虚假图片[全真，全假的标签]
        # Adversarial ground truths
        # 读取数据集中的真图片
        # 将tensor变成Variable放入计算图中，tensor变成variable之后才能进行反向传播求梯度
        target_real = Variable(Tensor(np.ones((real_A.size(0), *D_A.output_shape))), requires_grad=False) # 定义真实的图片label为1 ones((1, 1, 16, 16))
        target_fake = Variable(Tensor(np.zeros((real_A.size(0), *D_A.output_shape))), requires_grad=False) # 定义假的图片label为1 ones((1, 1, 16, 16))
 
        # ------------------
        #  Train Generators
        #  训练生成器
        #  Train Generator
        # 原理：目的是希望生成的假的图片被判别器判断为真的图片，
        # 在此过程中，将判别器固定，将假的图片传入判别器的结果与真实的label对应，
        # 反向传播更新的参数是生成网络里面的参数，
        # 这样可以通过更新生成网络里面的参数，来训练网络，使得生成的图片让判别器以为是真的, 这样就达到了对抗的目的
        # ------------------
 
        G_AB.train()
        G_BA.train()
 
        # 梯度清零，方便下代训练
        optimizer_G.zero_grad()
 
        # Identity loss ：用于保证生成图像的连续性，一个图像x，经过其中一个生成器生成图像 G(x)，尽可能与原来图像接近。
        # A风格的图像 放在 B -> A 生成器中，生成的图像也要是 A风格
        loss_id_A = criterion_identity(G_BA(real_A), real_A) 
        loss_id_B = criterion_identity(G_AB(real_B), real_B) # loss_id_A就是把图像A1放入 B2A 的生成器中，
                                                              # 那当然生成图像A2的风格也得是A风格, 要让A1,A2的差距很小 
        
        loss_identity = (loss_id_A + loss_id_B) / 2
         
        # GAN loss
        fake_B = G_AB(real_A) # 用真图像A生成的假图像B
        # loss_GAN_AB = criterion_GAN(D_B(fake_B), target_real) # 用B鉴别器鉴别假图像B，
                                                                # 训练生成器的目的就是要让鉴别器以为假的是真的，假的太接近真的让鉴别器分辨不出来
        loss_GAN_AB = -torch.mean(D_B(fake_B))
        
                                                        
        fake_A = G_BA(real_B) # 用真图像B生成的假图像A
        
        # loss_GAN_BA = criterion_GAN(D_A(fake_A), target_real) # 用A鉴别器鉴别假图像A，训练生成器的目的就是要让鉴别器以为假的是真的,
                                                        # 假的太接近真的让鉴别器分辨不出来
        loss_GAN_BA = -torch.mean(D_A(fake_A))
        loss_GAN = (loss_GAN_AB + loss_GAN_BA) / 2 # GAN loss
 
        # Cycle loss 循环一致性损失
        recov_A = G_BA(fake_B) # 之前中realA 通过 A -> B 生成的假图像B，再经过 B -> A ，使得fakeB 得到的循环图像recovA，
        loss_cycle_A = criterion_cycle(recov_A, real_A) # realA和recovA的差距应该很小，
                                                        # 以保证A,B间不仅风格有所变化，而且图片对应的的细节也可以保留
        recov_B = G_AB(fake_A)
        loss_cycle_B = criterion_cycle(recov_B, real_B) 
 
        loss_cycle = (loss_cycle_A + loss_cycle_B) / 2 
 
        # 总损失函数
        # Total loss
        loss_G = loss_GAN + arg.lambda_cyc * loss_cycle + arg.lambda_id * loss_identity # 就是上面所有的损失都加起来
 
        # 反向传播
        loss_G.backward() # 将误差反向传播
 
        # 权重更新
        optimizer_G.step() # 更新参数
 
        # -----------------------
        #  Train Discriminator A
        #  训练分类器A
        # 分为两部分：1、真的图像判别为真；2、假的图像判别为假
        # -----------------------
 
        optimizer_D_A.zero_grad() # 在反向传播之前，先将梯度归0
 
        # Real loss
        # loss_real = criterion_GAN(D_A(real_A), target_real)
        # Fake loss (on batch of previously generated samples)
        # 假的图像判别为假(从之前的buffer缓存中随机取一张)
        fake_A_ = fake_A_buffer.push_and_pop(fake_A)
        # loss_fake = criterion_GAN(D_A(fake_A_.detach()), target_fake)
        # Total loss
        # loss_D_A = (loss_real + loss_fake) / 2
        gradient_penalty_A = gp(D_A, real_A, fake_A_)
        loss_D_A = -torch.mean(D_A(real_A)) + torch.mean(D_A(fake_A_)) + gradient_penalty_A
        loss_D_A.backward()
        optimizer_D_A.step()
        
        # for p in D_A.parameters():
        #   p.data.clamp_(-clip_value, clip_value)
 
        # -----------------------
        #  Train Discriminator B
        #  训练分类器B
        # -----------------------
 
        optimizer_D_B.zero_grad()
         
        # Real loss
        # 真的图像判别为真
        # loss_real = criterion_GAN(D_B(real_B), target_real)
        # Fake loss (on batch of previously generated samples)
        fake_B_ = fake_B_buffer.push_and_pop(fake_B)
        # loss_fake = criterion_GAN(D_B(fake_B_.detach()), target_fake)
        gradient_penalty_B = gp(D_B, real_B, fake_B_)
        loss_D_B = -torch.mean(D_B(real_B)) + torch.mean(D_B(fake_B_)) + gradient_penalty_B
        # Total loss
        # loss_D_B = (loss_real + loss_fake) / 2
 
        loss_D_B.backward()
        optimizer_D_B.step()
        
        # for p in D_B.parameters():
        #   p.data.clamp_(-clip_value, clip_value)
 
        loss_D = (loss_D_A + loss_D_B) / 2
 
        # --------------
        #  Log Progress
        #  训练进程显示
        # --------------
 
        # Determine approximate time left
        # 确定剩下的大约时间  假设当前 epoch = 5， i = 100
        batches_done = epoch * len(dataloader) + i # 已经训练了多长时间 5 * 500 + 100 次
        batches_left = arg.n_epochs * len(dataloader) - batches_done # 还剩下 200 * 500 - 2600 次
        time_left = datetime.timedelta(seconds=batches_left * (time.time() - prev_time)) # 还需要的时间 time_left = 剩下的次数 * 每次的时间
        prev_time = time.time()
 
        # Print log
        #  打印日志Log Progress
        print(
            "\r[Epoch %d/%d] [Batch %d/%d] [D loss: %f] [G loss: %f, adv: %f, cycle: %f, identity: %f] ETA: %s"
            % (
                epoch,
                arg.n_epochs,
                i,
                len(dataloader),
                loss_D.item(),
                loss_G.item(),
                loss_GAN.item(),
                loss_cycle.item(),
                loss_identity.item(),
                time_left,
            )
        )
 
        # If at sample interval save image
        # 每训练100张就保存一组测试集中的图片
        if batches_done % arg.sample_interval == 0:
            sample_images(batches_done)
 
    # Update learning rates
    # 更新学习率
    lr_scheduler_G.step()
    lr_scheduler_D_A.step()
    lr_scheduler_D_B.step()
 
    if arg.checkpoint_interval != -1 and epoch % arg.checkpoint_interval == 0:
        # Save model checkpoints
        # 训练结束后，保存模型
        # 最好是每间隔几个epoch保存一次模型
        torch.save(G_AB.state_dict(), "saved_models/%s/G_AB_%d.pth" % (arg.dataset_name, epoch))
        torch.save(G_BA.state_dict(), "saved_models/%s/G_BA_%d.pth" % (arg.dataset_name, epoch))
        torch.save(D_A.state_dict(), "saved_models/%s/D_A_%d.pth" % (arg.dataset_name, epoch))
        torch.save(D_B.state_dict(), "saved_models/%s/D_B_%d.pth" % (arg.dataset_name, epoch))

  0%|          | 0/6287 [00:00<?, ?it/s]

[Epoch 0/200] [Batch 0/6287] [D loss: 165861472.000000] [G loss: 7.867941, adv: -0.260605, cycle: 0.548640, identity: 0.528430] ETA: 35 days, 1:03:35.592957
[Epoch 0/200] [Batch 1/6287] [D loss: 110826832.000000] [G loss: 7.798750, adv: -0.235622, cycle: 0.553853, identity: 0.499169] ETA: 24 days, 14:37:36.593430
[Epoch 0/200] [Batch 2/6287] [D loss: 72661648.000000] [G loss: 5.683390, adv: -0.236117, cycle: 0.395052, identity: 0.393797] ETA: 7 days, 0:00:07.771274
[Epoch 0/200] [Batch 3/6287] [D loss: 55306512.000000] [G loss: 6.248445, adv: -0.220068, cycle: 0.442810, identity: 0.408082] ETA: 6 days, 22:16:35.707652
[Epoch 0/200] [Batch 4/6287] [D loss: 26758316.000000] [G loss: 5.868272, adv: -0.238618, cycle: 0.417227, identity: 0.386924] ETA: 7 days, 0:19:48.268138
[Epoch 0/200] [Batch 5/6287] [D loss: 15852660.000000] [G loss: 6.630352, adv: -0.206149, cycle: 0.471462, identity: 0.424376] ETA: 6 days, 23:39:08.724624
[Epoch 0/200] [Batch 6/6287] [D loss: 10895138.000000] [G loss:

[Epoch 0/200] [Batch 53/6287] [D loss: 231428.218750] [G loss: 4.676363, adv: -0.024143, cycle: 0.311150, identity: 0.317801] ETA: 7 days, 0:41:34.754289
[Epoch 0/200] [Batch 54/6287] [D loss: 314117.218750] [G loss: 5.175102, adv: -0.043366, cycle: 0.353637, identity: 0.336420] ETA: 7 days, 0:41:39.367461
[Epoch 0/200] [Batch 55/6287] [D loss: 239939.000000] [G loss: 3.234017, adv: -0.039505, cycle: 0.227464, identity: 0.199776] ETA: 7 days, 2:47:18.810378
[Epoch 0/200] [Batch 56/6287] [D loss: 385572.093750] [G loss: 4.909492, adv: -0.033352, cycle: 0.331175, identity: 0.326218] ETA: 7 days, 0:20:44.745880
[Epoch 0/200] [Batch 57/6287] [D loss: 269786.250000] [G loss: 6.043445, adv: -0.041717, cycle: 0.407710, identity: 0.401611] ETA: 7 days, 2:26:26.276219
[Epoch 0/200] [Batch 58/6287] [D loss: 108941.921875] [G loss: 4.059468, adv: -0.034616, cycle: 0.281122, identity: 0.256573] ETA: 7 days, 0:41:25.744283
[Epoch 0/200] [Batch 59/6287] [D loss: 350449.031250] [G loss: 6.403365, adv

[Epoch 0/200] [Batch 107/6287] [D loss: 152042.546875] [G loss: 5.224533, adv: -0.000046, cycle: 0.354344, identity: 0.336228] ETA: 7 days, 18:22:28.914932
[Epoch 0/200] [Batch 108/6287] [D loss: 120293.117188] [G loss: 5.463492, adv: -0.000082, cycle: 0.367391, identity: 0.357934] ETA: 7 days, 18:50:48.929820
[Epoch 0/200] [Batch 109/6287] [D loss: 172964.359375] [G loss: 3.513202, adv: 0.000285, cycle: 0.238355, identity: 0.225873] ETA: 7 days, 18:29:52.693757
[Epoch 0/200] [Batch 110/6287] [D loss: 197985.453125] [G loss: 3.671960, adv: -0.003434, cycle: 0.248748, identity: 0.237582] ETA: 7 days, 18:50:49.058869
[Epoch 0/200] [Batch 111/6287] [D loss: 66336.906250] [G loss: 3.535882, adv: -0.008356, cycle: 0.248750, identity: 0.211348] ETA: 7 days, 19:53:43.414859
[Epoch 0/200] [Batch 112/6287] [D loss: 42887.078125] [G loss: 3.491517, adv: -0.013605, cycle: 0.241816, identity: 0.217392] ETA: 7 days, 20:56:28.472260
[Epoch 0/200] [Batch 113/6287] [D loss: 64368.363281] [G loss: 4.12

[Epoch 0/200] [Batch 160/6287] [D loss: 83115.375000] [G loss: 5.987823, adv: -0.011302, cycle: 0.400549, identity: 0.398726] ETA: 7 days, 22:40:53.644295
[Epoch 0/200] [Batch 161/6287] [D loss: 45068.718750] [G loss: 4.518598, adv: -0.005723, cycle: 0.304864, identity: 0.295136] ETA: 8 days, 3:35:41.594557
[Epoch 0/200] [Batch 162/6287] [D loss: 20248.181641] [G loss: 3.357546, adv: -0.004704, cycle: 0.238441, identity: 0.195568] ETA: 8 days, 3:32:44.782135
[Epoch 0/200] [Batch 163/6287] [D loss: 138544.140625] [G loss: 5.273471, adv: -0.005990, cycle: 0.358094, identity: 0.339705] ETA: 7 days, 23:01:46.754180
[Epoch 0/200] [Batch 164/6287] [D loss: 220553.921875] [G loss: 5.400583, adv: -0.011286, cycle: 0.365997, identity: 0.350379] ETA: 8 days, 0:46:31.032319
[Epoch 0/200] [Batch 165/6287] [D loss: 39785.597656] [G loss: 4.034111, adv: -0.006201, cycle: 0.279361, identity: 0.249340] ETA: 8 days, 1:07:30.321932
[Epoch 0/200] [Batch 166/6287] [D loss: 32644.876953] [G loss: 3.842441,

...

[Epoch 6/200] [Batch 4064/6287] [D loss: 15.940702] [G loss: 1.734933, adv: -0.008835, cycle: 0.118947, identity: 0.110859] ETA: 8 days, 5:23:54.288311
[Epoch 6/200] [Batch 4065/6287] [D loss: 14.826950] [G loss: 2.768595, adv: -0.010881, cycle: 0.189037, identity: 0.177821] ETA: 8 days, 7:21:49.484539
[Epoch 6/200] [Batch 4066/6287] [D loss: 15.646542] [G loss: 1.696697, adv: -0.010026, cycle: 0.117353, identity: 0.106638] ETA: 8 days, 5:14:22.454721
[Epoch 6/200] [Batch 4067/6287] [D loss: 17.303394] [G loss: 2.631492, adv: -0.003317, cycle: 0.179940, identity: 0.167082] ETA: 8 days, 15:17:21.211049
[Epoch 6/200] [Batch 4068/6287] [D loss: 8.206269] [G loss: 2.088310, adv: -0.005377, cycle: 0.149044, identity: 0.120649] ETA: 9 days, 2:28:07.877641
[Epoch 6/200] [Batch 4069/6287] [D loss: 11.827526] [G loss: 1.559973, adv: -0.004080, cycle: 0.109057, identity: 0.094697] ETA: 9 days, 5:42:05.973627
[Epoch 6/200] [Batch 4070/6287] [D loss: 18.767765] [G loss: 1.430436, adv: -0.006484, c

[Epoch 6/200] [Batch 4118/6287] [D loss: 11.180528] [G loss: 2.207951, adv: 0.002423, cycle: 0.153453, identity: 0.134199] ETA: 8 days, 22:22:09.886122
[Epoch 6/200] [Batch 4119/6287] [D loss: 4.520263] [G loss: 2.870323, adv: -0.008386, cycle: 0.209020, identity: 0.157703] ETA: 8 days, 22:28:46.003668
[Epoch 6/200] [Batch 4120/6287] [D loss: 21.592676] [G loss: 3.380712, adv: -0.012256, cycle: 0.229413, identity: 0.219768] ETA: 8 days, 22:07:47.586073
[Epoch 6/200] [Batch 4121/6287] [D loss: 11.586805] [G loss: 1.944815, adv: 0.000892, cycle: 0.134047, identity: 0.120690] ETA: 9 days, 0:09:57.730579
[Epoch 6/200] [Batch 4122/6287] [D loss: 17.354939] [G loss: 2.460262, adv: 0.004227, cycle: 0.169047, identity: 0.153113] ETA: 8 days, 21:38:51.218476
[Epoch 6/200] [Batch 4123/6287] [D loss: 13.110942] [G loss: 2.210876, adv: 0.000726, cycle: 0.139720, identity: 0.162590] ETA: 8 days, 23:07:42.526599
[Epoch 6/200] [Batch 4124/6287] [D loss: 8.149321] [G loss: 1.896414, adv: -0.004032, cy

[Epoch 6/200] [Batch 4172/6287] [D loss: 13.010126] [G loss: 2.016404, adv: -0.008304, cycle: 0.138598, identity: 0.127746] ETA: 9 days, 2:37:00.475021
[Epoch 6/200] [Batch 4173/6287] [D loss: 4.824584] [G loss: 3.356074, adv: -0.008283, cycle: 0.219737, identity: 0.233397] ETA: 9 days, 4:24:12.785184
[Epoch 6/200] [Batch 4174/6287] [D loss: 9.117337] [G loss: 2.214038, adv: -0.005887, cycle: 0.146007, identity: 0.151970] ETA: 9 days, 2:16:25.217033
[Epoch 6/200] [Batch 4175/6287] [D loss: 10.527357] [G loss: 1.934397, adv: -0.003563, cycle: 0.121016, identity: 0.145560] ETA: 9 days, 2:31:29.321476
[Epoch 6/200] [Batch 4176/6287] [D loss: 2.459249] [G loss: 1.623282, adv: -0.004877, cycle: 0.115422, identity: 0.094789] ETA: 9 days, 3:08:37.802477
[Epoch 6/200] [Batch 4177/6287] [D loss: 19.512606] [G loss: 2.140395, adv: -0.005993, cycle: 0.143412, identity: 0.142453] ETA: 9 days, 1:00:49.967180
[Epoch 6/200] [Batch 4178/6287] [D loss: 24.868755] [G loss: 1.904601, adv: 0.001307, cycle

[Epoch 6/200] [Batch 4226/6287] [D loss: 8.868341] [G loss: 1.660076, adv: -0.003432, cycle: 0.117540, identity: 0.097622] ETA: 9 days, 0:02:02.200788
[Epoch 6/200] [Batch 4227/6287] [D loss: 5.780522] [G loss: 1.847474, adv: -0.004373, cycle: 0.124306, identity: 0.121757] ETA: 9 days, 0:13:46.610508
[Epoch 6/200] [Batch 4228/6287] [D loss: 10.764272] [G loss: 1.815296, adv: -0.004572, cycle: 0.119052, identity: 0.125869] ETA: 9 days, 1:46:55.359771
[Epoch 6/200] [Batch 4229/6287] [D loss: 7.938728] [G loss: 2.772384, adv: -0.008028, cycle: 0.181766, identity: 0.192550] ETA: 9 days, 0:03:14.176535
[Epoch 6/200] [Batch 4230/6287] [D loss: 18.947630] [G loss: 2.744659, adv: -0.011451, cycle: 0.202230, identity: 0.146761] ETA: 9 days, 0:11:16.608849


KeyboardInterrupt: 

In [ ]:
from torchsummary import summary


model = GeneratorResNet(input_shape, arg.n_residual_blocks).cuda()
summary(model, input_size=(arg.channels, arg.img_height, arg.img_width), batch_size=-1)

In [ ]:
from torchsummary import summary # 第三方库打印模型参数

model = Discriminator(input_shape).cuda()
summary(model, input_size=(arg.channels, arg.img_height, arg.img_width), batch_size=-1)